In [36]:
import os
import tarfile
from pathlib import Path

import anndata as ad
import cellestial as cl
import requests
import scanpy as sc
from lets_plot import *
from tqdm import tqdm

LetsPlot.setup_html()


In [4]:
print(
    red("Hello World!"),
    cyan("Hello World!"),
    green("Hello World!"),
    yellow("Hello World!"),
)

Hello World! Hello World! Hello World! Hello World!


## 1. Downloading the Dataset and Loading the Data

__Note:__
Sample name includes the developmental stage in weeks and the internal ID.
week8_001 – this sample is collected from week 8 of development and ID is 001.
Some developmental stages have replicates.

Kameneva P, Artemov AV, Kastriti ME, Faure L et al. 
Single-cell transcriptomics of human embryos identifies multiple sympathoblast 
lineages with potential implications for neuroblastoma origin. 
Nat Genet 2021 May;53(5):694-706. 

Main link for the dataset: 
https://www.ncbi.nlm.nih.gov/geo/query/acc.cgi?acc=GSE147821

In [5]:
# direct download link
dataset_url = "https://www.ncbi.nlm.nih.gov/geo/download/?acc=GSE147821&format=file"

In [6]:
# create the processed directory if it doesn't exist and set the path to the concatenated file
processed_dir = Path("data/processed")
processed_dir.mkdir(exist_ok=True, parents=True)
concat_file = processed_dir / "concatenated.h5ad"

In [7]:
# dictionary to map sample identifiers to sample properties
files = {
    "GSM4446535": "week8_001",
    "GSM4446536": "week9_063",
    "GSM4446537": "week6_088",
    "GSM4446538": "week14_123",
    "GSM4446539": "week12_124",
    "GSM4446540": "week8_125",
    "GSM4446541": "week9_005",
    "GSM4446542": "week11_006",
    "GSM4446543": "week9_007",
    "GSM4734601": "week8_016",
    "GSM4734602": "week9_031_paraganglia",
    "GSM4734603": "week12_035",
    "GSM4734604": "week12_036_extraadrenal",
}

In [8]:
files

{'GSM4446535': 'week8_001',
 'GSM4446536': 'week9_063',
 'GSM4446537': 'week6_088',
 'GSM4446538': 'week14_123',
 'GSM4446539': 'week12_124',
 'GSM4446540': 'week8_125',
 'GSM4446541': 'week9_005',
 'GSM4446542': 'week11_006',
 'GSM4446543': 'week9_007',
 'GSM4734601': 'week8_016',
 'GSM4734602': 'week9_031_paraganglia',
 'GSM4734603': 'week12_035',
 'GSM4734604': 'week12_036_extraadrenal'}

In [ ]:
def get_dataset(url: str, name: str, folder: str = "data/raw") -> None:
    """
    Get the Dataset from the URL.

    Parameters
    ----------
    url : str
        URL of the Dataset.
    name : str
        Name of the Dataset to save.
    folder : str, optional
        Folder to save the Dataset, by default "data/raw"

    """
    ref_dir = Path(folder)
    ref_dir.mkdir(exist_ok=True, parents=True)
    response = requests.get(url, stream=True)
    output_path = ref_dir / name
    # Check if the file already exists
    total_size = int(response.headers.get("content-length", 0))
    if output_path.exists() and os.stat(output_path).st_size == total_size:
        print(f"{output_path} already exists, skipping downloading...")
    else:
        # Download the file
        with (
            Path.open(output_path, "wb") as f,
            tqdm(  # progress bar
                desc="Downloading",
                total=total_size,
                unit="B",
                unit_scale=True,
                unit_divisor=1024,
                colour="green",
            ) as bar,
        ):
            for chunk in response.iter_content(chunk_size=8192):
                if chunk:
                    f.write(chunk)
                    bar.update(len(chunk))

    return

### Fetch the dataset

In [ ]:
get_dataset(dataset_url, name="GSE147821_RAW.tar")

### Extract the tar file

In [ ]:
with tarfile.open("data/raw/GSE147821_RAW.tar", "r") as tar:
    tar.extractall("data/raw/GSE147821_RAW")

## 2. Performing data normalization (consider cell cycle correction) and quality control,data cleaning.

### Quality control

In [38]:
def filter_pp_qc(sample: ad.AnnData):
    # Filtering for cell and genes
    sample.var_names_make_unique()
    sc.pp.filter_cells(sample, min_genes=200)
    sc.pp.filter_genes(sample, min_cells=3)
    # mitochondrial genes
    sample.var["mt"] = sample.var_names.str.startswith("MT-")
    # ribosomal genes
    sample.var["ribo"] = sample.var_names.str.startswith(("RPS", "RPL"))
    # hemoglobin genes
    sample.var["hb"] = sample.var_names.str.contains("^HB[^(P)]")
    sc.pp.calculate_qc_metrics(sample, qc_vars=["mt", "ribo", "hb"], inplace=True)
    # Remove cells with high mitochondrial gene percentage
    sample = sample[sample.obs.pct_counts_mt < 15, :]
    # Optional: filter based on percent mitochondria or number of genes
    sc.pp.normalize_total(sample, target_sum=1e4)
    sc.pp.log1p(sample)
    sc.pp.highly_variable_genes(sample, flavor='seurat', n_top_genes=2000)

    return sample

In [39]:
s1 = sc.read_10x_h5("data/raw/GSE147821_RAW/GSM4446535_10X_19_001.raw_feature_bc_matrix.h5")

/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/anndata/_core/anndata.py:1758: UserWarning: Variable names are not unique. To make them unique, call `.var_names_make_unique`.
  utils.warn_names_duplicates("var")
/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/anndata/_core/anndata.py:1758: UserWarning: Variable names are not unique. To make them unique, call `.var_names_make_unique`.
  utils.warn_names_duplicates("var")


In [40]:
s1

AnnData object with n_obs × n_vars = 6794880 × 33538
    var: 'gene_ids', 'feature_types', 'genome'

In [41]:
s1_filtered = filter_pp_qc(s1)

/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/scanpy/preprocessing/_normalization.py:216: UserWarning: Received a view of an AnnData. Making a copy.
  view_to_actual(adata)


In [42]:
s1

AnnData object with n_obs × n_vars = 7879 × 22582
    obs: 'n_genes', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes', 'total_counts_mt', 'log1p_total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'log1p_total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'log1p_total_counts_hb', 'pct_counts_hb'
    var: 'gene_ids', 'feature_types', 'genome', 'n_cells', 'mt', 'ribo', 'hb', 'n_cells_by_counts', 'mean_counts', 'log1p_mean_counts', 'pct_dropout_by_counts', 'total_counts', 'log1p_total_counts'

In [ ]:
cl.violins(
    s1,
    ["n_genes_by_counts", "total_counts", "pct_counts_mt"],
)


In [45]:
def concat_h5_files(
    files: dict, raw_dir="data/raw/GSE147821_RAW", out_dir="data/processed"
):
    concat_file = Path(out_dir) / "concatenated.h5ad"
    if not Path(concat_file).exists():
        samples = []
        for key in files:
            # find the file
            h5_file = [key for key in os.listdir(raw_dir) if key.startswith(key)][0]
            # find the matching info
            info = files[key]
            # extract the information from the file name
            week_str = info.split("_")[0]  # gets the week as string
            week = week_str.split("week")[1]  # converts to integer
            sample_name = info.split("_")[1]  # gets the sample name

            # assign the full path
            full_path = Path(raw_dir) / h5_file

            # read the file
            sample = filter_pp_qc(sc.read_10x_h5(full_path))  # filter the sample
            sample.obs_names = [f"{info}_{cell}" for cell in sample.obs_names]

            # Add metadata
            sample.obs["sample_id"] = sample_name
            sample.obs["week"] = week
            sample.obs["filename"] = h5_file

            # append to the list
            samples.append(sample)
        # concatenate the samples
        adt = ad.concat(
            samples,
            join="outer",
            label="sample",
            keys=[sample.obs["sample_id"][0] for sample in samples],
        )
        # save the file
        adt.write_h5ad(concat_file)
    else:
        adt = ad.read_h5ad(concat_file)

    return adt

In [53]:
adt = concat_h5_files(files)

In [54]:
adt.raw = adt

In [55]:
adt

AnnData object with n_obs × n_vars = 99073 × 22639
    obs: 'n_genes', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'total_counts', 'log1p_total_counts', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_100_genes', 'pct_counts_in_top_200_genes', 'pct_counts_in_top_500_genes', 'total_counts_mt', 'log1p_total_counts_mt', 'pct_counts_mt', 'total_counts_ribo', 'log1p_total_counts_ribo', 'pct_counts_ribo', 'total_counts_hb', 'log1p_total_counts_hb', 'pct_counts_hb', 'sample_id', 'week', 'filename', 'sample'

## 3. Generate the UMAP and perform cluster annotation.

Take a note of the clusters on Figure 1b https://www.nature.com/articles/s41588-
021-00818-x for marker genes.

In [56]:
# 1. Scale the data
sc.pp.scale(adt, max_value=10)
# 2. PCA
sc.tl.pca(adt, svd_solver='arpack')
# 3. Compute neighbors
sc.pp.neighbors(adt, n_neighbors=25, n_pcs=50)
# 4. Run UMAP
sc.tl.umap(adt)

/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/sklearn/manifold/_spectral_embedding.py:329: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(
/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/sklearn/manifold/_spectral_embedding.py:455: UserWarning: Exited at iteration 227 with accuracies 
[2.61421107e-14 3.92688119e-05 2.99238629e-05 1.85325225e-05]
not reaching the requested tolerance 1.946091651916504e-05.
Use iteration 163 instead with accuracy 
1.7966581093370254e-05.

  _, diffusion_map = lobpcg(
/Users/zaf4/dev/CCRItask/.venv/lib/python3.13/site-packages/sklearn/manifold/_spectral_embedding.py:455: UserWarning: Exited postprocessing with accuracies 
[1.83971808e-15 4.11463354e-05 1.08913733e-05 1.98286156e-05]
not reaching the requested tolerance 1.946091651916504e-05.
  _, diffusion_map = lobpcg(


In [50]:
adt.obs.head()

n_genes  n_genes_by_counts  \
week8_001_AAACCCAAGCTTTCCC-1      223                223   
week8_001_AAACCCAAGTAACCTC-1     1760               1760   
week8_001_AAACCCAAGTGCTACT-1     3626               3626   
week8_001_AAACCCACAGATCATC-1     2856               2856   
week8_001_AAACCCACATATGGCT-1      214                214   

                              log1p_n_genes_by_counts  total_counts  \
week8_001_AAACCCAAGCTTTCCC-1                 5.411646         277.0   
week8_001_AAACCCAAGTAACCTC-1                 7.473637        5228.0   
week8_001_AAACCCAAGTGCTACT-1                 8.196161       12497.0   
week8_001_AAACCCACAGATCATC-1                 7.957527        7170.0   
week8_001_AAACCCACATATGGCT-1                 5.370638        2224.0   

                              log1p_total_counts  pct_counts_in_top_50_genes  \
week8_001_AAACCCAAGCTTTCCC-1            5.627621                   37.545126   
week8_001_AAACCCAAGTAACCTC-1            8.561975                   33.817904   
week8_001_AAACCCAAGTGCTACT-1            9.433324                   27.598624   
week8_001_AAACCCACAGATCATC-1            8.877800                   25.383543   
week8_001_AAACCCACATATGGCT-1            7.707512                   92.625899   

                              pct_counts_in_top_100_genes  \
week8_001_AAACCCAAGCTTTCCC-1                    55.595668   
week8_001_AAACCCAAGTAACCTC-1                    45.753634   
week8_001_AAACCCAAGTGCTACT-1                    37.753061   
week8_001_AAACCCACAGATCATC-1                    34.546722   
week8_001_AAACCCACATATGGCT-1                    94.874101   

                              pct_counts_in_top_200_genes  \
week8_001_AAACCCAAGCTTTCCC-1                    91.696751   
week8_001_AAACCCAAGTAACCTC-1                    57.230298   
week8_001_AAACCCAAGTGCTACT-1                    47.923502   
week8_001_AAACCCACAGATCATC-1                    44.072524   
week8_001_AAACCCACATATGGCT-1                    99.370504   

                              pct_counts_in_top_500_genes  total_counts_mt  \
week8_001_AAACCCAAGCTTTCCC-1                   100.000000             25.0   
week8_001_AAACCCAAGTAACCTC-1                    72.991584            731.0   
week8_001_AAACCCAAGTGCTACT-1                    61.830839           1235.0   
week8_001_AAACCCACAGATCATC-1                    59.246862            211.0   
week8_001_AAACCCACATATGGCT-1                   100.000000             19.0   

                              ...  total_counts_ribo  log1p_total_counts_ribo  \
week8_001_AAACCCAAGCTTTCCC-1  ...               45.0                 3.828641   
week8_001_AAACCCAAGTAACCTC-1  ...             1434.0                 7.268920   
week8_001_AAACCCAAGTGCTACT-1  ...             2310.0                 7.745436   
week8_001_AAACCCACAGATCATC-1  ...             1286.0                 7.160069   
week8_001_AAACCCACATATGGCT-1  ...               35.0                 3.583519   

                              pct_counts_ribo  total_counts_hb  \
week8_001_AAACCCAAGCTTTCCC-1        16.245487             13.0   
week8_001_AAACCCAAGTAACCTC-1        27.429226             13.0   
week8_001_AAACCCAAGTGCTACT-1        18.484436             13.0   
week8_001_AAACCCACAGATCATC-1        17.935844             16.0   
week8_001_AAACCCACATATGGCT-1         1.573741           1950.0   

                              log1p_total_counts_hb  pct_counts_hb  sample_id  \
week8_001_AAACCCAAGCTTTCCC-1               2.639057       4.693141        001   
week8_001_AAACCCAAGTAACCTC-1               2.639057       0.248661        001   
week8_001_AAACCCAAGTGCTACT-1               2.639057       0.104025        001   
week8_001_AAACCCACAGATCATC-1               2.833213       0.223152        001   
week8_001_AAACCCACATATGGCT-1               7.576097      87.679855        001   

                              week  \
week8_001_AAACCCAAGCTTTCCC-1     8   
week8_001_AAACCCAAGTAACCTC-1     8   
week8_001_AAACCCAAGTGCTACT-1     8   
week8_001_AAACCCACAGATCATC-1     8 

In [52]:
cl.umap(adt, 'week')

## 4. Visualize the data on the dot plot showing the 5 top differentially expressed genes per cluster

## 5. Sub-select adrenal medulla clusters (Schwann cell precursors (SCPs),Chromaffin cells, Sympathoblasts) and re-cluster them to improve the resolution of transitions.

Similar to re-clustering on Figure 2 https://www.nature.com/articles/s41588-021-
00818-x. Note that not all datasets may be included in the re-clustering. 
If you choose to do so, explain why that may be necessary.

For the last task, you can choose between two alternatives 
 
6a. Perform the trajectory analysis between SCPs and chromaffin cells, SCPs and 
sympathoblasts, and between chromaffin cells and sympathoblasts.  
Plot the important gene changes along the trajectories on heatmaps. 
You can use any trajectory analysis tool. Please explain your choice. 
 
6b. Using the SCENIC tool, analyse the regulons in SCPs, chromaffin cells, and 
sympathoblasts.  
Visualize important regulons whose activity spans the transitions between the 
clusters. Compare the regulon's expression to the expression of the 
corresponding transcription factors.

### 6a. Perform the trajectory analysis between SCPs and chromaffin cells, SCPs and sympathoblasts, and between chromaffin cells and sympathoblasts. Plot the important gene changes along the trajectories on heatmaps. You can use any trajectory analysis tool. Please explain your choice.

## 7. Generate the report:
7a. Please provide annotated code, documentation, results, and plots organized
in a PDF file.  
7b. Please provide short explanations of why you chose specific methods of
analysis.  
7c. Please provide a short, plausible interpretation of the results of task 6.  
7d. Please provide a small abstract of the overall results of the analysis (max 150
words).  